In [ ]:
import pandas as pd
import numpy as np
from tqdm import tqdm
tqdm.pandas(desc="progress-bar")
from gensim.models import Doc2Vec
from sklearn import utils
from sklearn.model_selection import train_test_split
import gensim
from sklearn.linear_model import LogisticRegression
from gensim.models.doc2vec import TaggedDocument
import re
import seaborn as sns
import matplotlib.pyplot as plt

In [ ]:
df=pd.read_csv('/content/drive/MyDrive/BTP/ecommerceDataset.csv')

In [ ]:
df

Household  \
0        Household   
1        Household   
2        Household   
3        Household   
4        Household   
...            ...   
50419  Electronics   
50420  Electronics   
50421  Electronics   
50422  Electronics   
50423  Electronics   

      Paper Plane Design Framed Wall Hanging Motivational Office Decor Art Prints (8.7 X 8.7 inch) - Set of 4 Painting made up in synthetic frame with uv textured print which gives multi effects and attracts towards it. This is an special series of paintings which makes your wall very beautiful and gives a royal touch. This painting is ready to hang, you would be proud to possess this unique painting that is a niche apart. We use only the most modern and efficient printing technology on our prints, with only the and inks and precision epson, roland and hp printers. This innovative hd printing technique results in durable and spectacular looking prints of the highest that last a lifetime. We print solely with top-notch 100% inks, to achieve brilliant and true colours. Due to their high level of uv resistance, our prints retain their beautiful colours for many years. Add colour and style to your living space with this digitally printed painting. Some are for pleasure and some for eternal bliss.so bring home this elegant print that is lushed with rich colors that makes it nothing but sheer elegance to be to your friends and family.it would be treasured forever by whoever your lucky recipient is. Liven up your place with these intriguing paintings that are high definition hd graphic digital prints for home, office or any room.  
0      SAF 'Floral' Framed Painting (Wood, 30 inch x ...                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          
1      SAF 'UV Textured Modern Art Print Framed' Pain...                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                  

In [ ]:
df.columns = ['Product','narrative']

In [ ]:
from sklearn import preprocessing
  
# label_encoder object knows how to understand word labels.
label_encoders = preprocessing.LabelEncoder()
  
# Encode labels in column 'species'.
df['Product']= label_encoders.fit_transform(df['Product'])

In [ ]:
df

Product                                          narrative
0            3  SAF 'Floral' Framed Painting (Wood, 30 inch x ...
1            3  SAF 'UV Textured Modern Art Print Framed' Pain...
2            3  SAF Flower Print Framed Painting (Synthetic, 1...
3            3  Incredible Gifts India Wooden Happy Birthday U...
4            3  Pitaara Box Romantic Venice Canvas Painting 6m...
...        ...                                                ...
50419        2  Strontium MicroSD Class 10 8GB Memory Card (Bl...
50420        2  CrossBeats Wave Waterproof Bluetooth Wireless ...
50421        2  Karbonn Titanium Wind W4 (White) Karbonn Titan...
50422        2  Samsung Guru FM Plus (SM-B110E/D, Black) Colou...
50423        2                   Micromax Canvas Win W121 (White)

[50424 rows x 2 columns]

In [ ]:
def print_complaint(index):
    example = df[df.index == index][['narrative', 'Product']].values[0]
    if len(example) > 0:
        print(example[0])
        print('Product:', example[1])
print_complaint(12)

Painting Mantra 'Vintage Car' Art Printing Set (Synthetic Wood, 60 cm x 50 cm x 2 cm, Brown, Set of 4) Size:60 cm x 50 cm x 2 cm   From the house of art street, we bring this exclusive framed poster to satiate the taste of decor freaks and vintage cars lovers. The filling station-vintage car brown framed poster is a high resolution vintage poster which comes covered in a brown frame. Hang the framed posters depicting image of a car from the nostalgic era on your favourite wall and make it look colourful and vibrant. The product is durable and of high quality. Presented to you with love from art street.
Product: 3


In [ ]:
df.narrative=df.narrative.astype(str)

In [ ]:
from bs4 import BeautifulSoup
def cleanText(text):
    text = BeautifulSoup(text, "lxml").text
    text = re.sub(r'\|\|\|', r' ', text) 
    text = re.sub(r'http\S+', r'<URL>', text)
    text = text.lower()
    text = text.replace('x', '')
    return text
df['narrative'] = df['narrative'].apply(cleanText)

In [ ]:
import nltk
nltk.download('punkt')

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.


True

In [ ]:
train, test = train_test_split(df, test_size=0.3, random_state=42)
import nltk
from nltk.corpus import stopwords
def tokenize_text(text):
    tokens = []
    for sent in nltk.sent_tokenize(text):
        for word in nltk.word_tokenize(sent):
            if len(word) < 2:
                continue
            tokens.append(word.lower())
    return tokens
train_tagged = train.apply(
    lambda r: TaggedDocument(words=tokenize_text(r['narrative']), tags=[r.Product]), axis=1)
test_tagged = test.apply(
    lambda r: TaggedDocument(words=tokenize_text(r['narrative']), tags=[r.Product]), axis=1)

In [ ]:
import multiprocessing
cores = multiprocessing.cpu_count()

In [ ]:
model_dbow = Doc2Vec(dm=0, vector_size=300, negative=5, hs=0, min_count=2, sample = 0, workers=cores)
model_dbow.build_vocab([x for x in tqdm(train_tagged.values)])

100%|██████████| 35296/35296 [00:00<00:00, 1676524.63it/s]


In [ ]:
%%time
for epoch in range(30):
    model_dbow.train(utils.shuffle([x for x in tqdm(train_tagged.values)]), total_examples=len(train_tagged.values), epochs=1)
    model_dbow.alpha -= 0.002
    model_dbow.min_alpha = model_dbow.alpha

100%|██████████| 35296/35296 [00:00<00:00, 2024729.60it/s]


CPU times: user 8min 14s, sys: 8.05 s, total: 8min 22s
Wall time: 4min 52s


In [ ]:
def vec_for_learning(model, tagged_docs):
    sents = tagged_docs.values
    targets, regressors = zip(*[(doc.tags[0], model.infer_vector(doc.words, steps=20)) for doc in sents])
    return targets, regressors
    

In [ ]:
y_train, X_train = vec_for_learning(model_dbow, train_tagged)


In [ ]:
y_test, X_test = vec_for_learning(model_dbow, test_tagged)

In [ ]:
from sklearn.neural_network import MLPClassifier
from sklearn.datasets import make_classification
from sklearn.model_selection import train_test_split

In [ ]:
clf = MLPClassifier(random_state=1, max_iter=300).fit(X_train, y_train)


In [ ]:
y_pred=clf.predict(X_test)

In [ ]:
from sklearn.metrics import classification_report

In [ ]:
print(classification_report(y_test, y_pred))

              precision    recall  f1-score   support

           0       0.46      0.47      0.47      3552
           1       0.40      0.36      0.38      2580
           2       0.41      0.44      0.43      3152
           3       0.55      0.56      0.56      5844

    accuracy                           0.48     15128
   macro avg       0.46      0.46      0.46     15128
weighted avg       0.48      0.48      0.48     15128



In [ ]:
from sklearn.ensemble import RandomForestClassifier

In [ ]:
clf = RandomForestClassifier(n_estimators = 100) 
 
# Training the model on the training dataset
# fit function is used to train the model using the training sets as parameters
clf.fit(X_train, y_train)
 

RandomForestClassifier()

In [ ]:
y_pred=clf.predict(X_test)

In [ ]:
from sklearn.metrics import confusion_matrix

In [ ]:
from sklearn.metrics import classification_report

In [ ]:
print(classification_report(y_test, y_pred))

              precision    recall  f1-score   support

           0       0.52      0.40      0.45      3552
           1       0.47      0.35      0.40      2580
           2       0.45      0.35      0.39      3152
           3       0.51      0.70      0.59      5844

    accuracy                           0.50     15128
   macro avg       0.49      0.45      0.46     15128
weighted avg       0.49      0.50      0.48     15128



In [ ]:
from sklearn.svm import LinearSVC


In [ ]:
X_train

(array([ 0.05911811, -0.07248382, -0.02654511,  0.2401846 ,  0.30725282,
         0.56586987, -0.35289842, -1.2231251 ,  0.21401142,  0.50728685,
        -1.3181762 , -0.41863385,  0.6484116 , -0.23103286, -0.05578875,
        -0.3487687 ,  1.16886   ,  0.2907294 ,  0.35607576, -0.18007503,
         0.17147796,  0.7106648 , -0.25669676,  0.7590959 , -0.4408921 ,
        -0.2027657 ,  0.02643663, -0.5571976 ,  0.20711742, -0.5604983 ,
         0.11797255,  1.3159913 ,  0.19135617,  0.2302542 ,  0.33077922,
         0.8247923 , -0.0389273 , -0.5661065 , -0.00862228,  0.6351087 ,
        -0.46965644,  0.34208357, -0.9001977 ,  0.09813623, -0.5289904 ,
         0.09293582, -0.8834775 ,  0.42547134,  0.24820304,  0.1820717 ,
         0.02748092,  0.4379594 , -0.7189308 , -0.69354093,  1.085249  ,
        -0.25315896, -0.634572  ,  0.73263186, -0.1139765 , -0.47525102,
        -0.64343584,  0.18620206, -0.75773144,  0.18009181, -0.30834484,
        -0.4291403 ,  0.2705152 , -0.13270077, -0.4

In [ ]:
X_train_1=np.vstack(X_train)

In [ ]:
X_test_1=np.vstack(X_test)

In [ ]:
X_train_1.shape


(35296, 300)

LabelEncoder()

In [ ]:
y_train

array([2, 2, 3, ..., 1, 3, 3])

In [ ]:
lsvc = LinearSVC(verbose=0)

In [ ]:
lsvc.fit(X_train_1, y_train)


/usr/local/lib/python3.7/dist-packages/sklearn/svm/_base.py:1208: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  ConvergenceWarning,


LinearSVC()

In [ ]:
score = lsvc.score(X_test_1, y_test)
print("Score: ", score)

Score:  0.502181385510312


In [ ]:
y_test

(1,
 3,
 0,
 1,
 2,
 3,
 0,
 1,
 0,
 3,
 1,
 3,
 2,
 3,
 0,
 3,
 0,
 3,
 3,
 2,
 3,
 0,
 2,
 0,
 3,
 0,
 0,
 0,
 1,
 3,
 2,
 1,
 0,
 1,
 0,
 0,
 3,
 0,
 3,
 2,
 2,
 2,
 2,
 0,
 3,
 2,
 1,
 3,
 2,
 2,
 3,
 3,
 2,
 1,
 0,
 2,
 3,
 0,
 1,
 0,
 3,
 3,
 1,
 1,
 3,
 0,
 3,
 2,
 0,
 1,
 2,
 3,
 3,
 0,
 0,
 1,
 0,
 2,
 2,
 2,
 3,
 2,
 3,
 2,
 0,
 0,
 3,
 3,
 0,
 2,
 1,
 2,
 1,
 2,
 3,
 0,
 3,
 1,
 3,
 0,
 1,
 3,
 3,
 0,
 2,
 0,
 3,
 1,
 3,
 2,
 3,
 0,
 3,
 3,
 3,
 0,
 3,
 2,
 3,
 3,
 0,
 0,
 0,
 1,
 2,
 3,
 2,
 0,
 2,
 3,
 2,
 1,
 3,
 3,
 1,
 3,
 1,
 0,
 3,
 1,
 0,
 3,
 1,
 3,
 1,
 3,
 1,
 0,
 0,
 0,
 0,
 3,
 3,
 2,
 2,
 3,
 2,
 3,
 3,
 0,
 2,
 3,
 2,
 0,
 0,
 1,
 2,
 3,
 3,
 3,
 3,
 2,
 2,
 2,
 3,
 3,
 3,
 1,
 3,
 0,
 0,
 0,
 2,
 0,
 2,
 2,
 2,
 2,
 3,
 1,
 3,
 0,
 2,
 3,
 3,
 1,
 1,
 3,
 3,
 0,
 3,
 3,
 3,
 2,
 1,
 0,
 2,
 0,
 3,
 3,
 0,
 0,
 0,
 3,
 0,
 3,
 3,
 2,
 1,
 0,
 3,
 1,
 0,
 0,
 0,
 0,
 3,
 3,
 3,
 0,
 3,
 3,
 3,
 0,
 0,
 0,
 3,
 3,
 0,
 3,
 2,
 0,
 0,
 3,
 3,
 0,
 0,
 0,
 1,
 3,


In [ ]:
from sklearn.metrics import classification_report

In [ ]:
y_pred=lsvc.predict(X_train_1)

In [ ]:
print(classification_report(y_train, y_pred))

              precision    recall  f1-score   support

           0       0.55      0.42      0.48      8268
           1       0.47      0.25      0.33      6091
           2       0.48      0.32      0.39      7469
           3       0.50      0.77      0.61     13468

    accuracy                           0.51     35296
   macro avg       0.50      0.44      0.45     35296
weighted avg       0.51      0.51      0.48     35296



In [ ]:
import nltk
nltk.download('punkt')
from nltk.tokenize import word_tokenize
import numpy as np

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [ ]:
sentence=np.array(train['narrative'])

In [ ]:
sentence

array(["acer 18.5 inch (46.99 cm) led monitor - eb192q (black) specifications led 18.5 '' acer eb192qb (b). brand acer model eb192qb response time 5 ms ma. resolution 1366768 @ 60hz contrast ratio 100 million: 1 (acm). brightness 200 nits (cd / m2). display 18.5 inch color system 16.7 m power supply (100v-240v): internal power consumption (off): 0.45w power consumption (sleep): 14w power consumption (on): 18w. vga port 1 port.",
       'soumik electricals 5-inch subwoofer with maimum 4 ohm(100 w) thisb product is from the brand soumik electricals it presents a 5 inch subwoofer with maimum 4 ohm and comes with 100w. use in your home theatre.',
       'santosha decor mdf wall decoration intersecting floating shelf rack (brown) - set of 3',
       ...,
       "tucute women's beautiful checks print with border feeding/maternity / nursing nighty/nightwear. rela at ease wearing this soft and comfortable maternity feeding nightwear dress from tucute. it's surely going to be your favourite nig

In [ ]:
len(sentence)

35296

In [ ]:
from nltk.tokenize import word_tokenize

#tokenized_sent = sentence
for i in range(len(sentence)):
  tokenized_sent+=word_tokenize(sentence[i])


In [ ]:
tokenized_sent

['maharsh',
 '220-240',
 'v',
 ',',
 '50',
 'hz',
 ',',
 '1000',
 'w',
 'blowing',
 'and',
 'sucking',
 'dual',
 'purpose',
 'vacuum',
 'cleaner',
 '(',
 'red',
 ')',
 'does',
 'making',
 'your',
 'house',
 'or',
 'car',
 'squeaky',
 'clean',
 'stress',
 'you',
 'so',
 'much',
 '?',
 'worry',
 'no',
 'more',
 'because',
 'the',
 '1000w',
 'power',
 'vacuum',
 'cleaner',
 'is',
 'here',
 'to',
 'the',
 'rescue',
 '!',
 'this',
 'vacuum',
 'cleaner',
 'is',
 'ideal',
 'for',
 'home',
 ',',
 'office',
 ',',
 'and',
 'car',
 'use',
 'as',
 'it',
 'effectively',
 'picks',
 'up',
 'the',
 'dust',
 'and',
 'dirt',
 'from',
 'floors',
 'and',
 'other',
 'surfaces',
 '.',
 'its',
 'powerful',
 'suction',
 'feature',
 'allows',
 'you',
 'to',
 'clean',
 'even',
 'the',
 'inaccessible',
 'nooks',
 'so',
 'dust',
 'and',
 'dirt',
 'could',
 'never',
 'hide',
 'anymore',
 '.',
 'you',
 'can',
 'now',
 'bid',
 'goodbye',
 'to',
 'your',
 'traditional',
 'cleaning',
 'materials',
 '!',
 'this',
 'vac

In [ ]:
from nltk.tokenize import sent_tokenize


In [ ]:
train.narrative=train.narrative.astype(str)

In [ ]:
sent_tokenize(np.array(train['narrative'][0]))

KeyError: ignored

In [ ]:
# import
from gensim.models.doc2vec import Doc2Vec, TaggedDocument
tagged_data = [TaggedDocument(d, [i]) for i, d in enumerate(tokenized_sent)]
tagged_data

NameError: ignored